In [1]:
import pandas as pd
import plotly.express as px
import numpy as np
import tensorflow as tf

https://www.sidc.be/SILSO/infosnmtot

Filename: SN_m_tot_V2.0.csv

Format: Comma Separated values (adapted for import in spreadsheets)

The separator is the semicolon ';'.

Contents:
Column 1-2: Gregorian calendar date
- Year
- Month

Column 3: Date in fraction of year.

Column 4: Monthly mean total sunspot number.

Column 5: Monthly mean standard deviation of the input sunspot numbers.

Column 6: Number of observations used to compute the monthly mean total sunspot number.

Column 7: Definitive/provisional marker. '1' indicates that the value is definitive. '0' indicates that the value is still provisional.

In [20]:
# read data
df = pd.read_csv('data/SN_m_tot_V2.0.csv', sep=';', header=None,names=['Year','Month','Date','mean','mean_std','observations','Definitive_provisional '])
# cut data from 1818
df = df[df['Year']>=1818]
df['Time'] = df['Month'].astype(str) +"/"+ df["Year"].astype(str)

In [21]:
fig = px.line(df, x="Time", y="mean", title='Total Sun plot')
fig.show()

### Data Transformation

In [86]:
def transform( df , smooth, step, y='value',x='time'):
    if (smooth=='MA'):
        newdf = df[[x]].copy();
        newdf['smooth'] = df[y].rolling(step, min_periods=1).mean()
        return newdf;
    elif (smooth=='WMA'):
        return df;
    else:
        return df;
        
            

In [87]:
STEP = 13
smoothdata = transform(df, 'MA', STEP, 'mean', 'Time')

plotdata = smoothdata.copy();
plotdata['raw'] = df['mean']
fig = px.line(plotdata, x="Time", y=["raw","smooth"], title='Total Sun plot')
fig.show()

In [88]:
smoothdata

Time     smooth
828    1/1818  58.100000
829    2/1818  47.750000
830    3/1818  45.966667
831    4/1818  48.850000
832    5/1818  56.780000
...       ...        ...
3287  12/2022  81.838462
3288   1/2023  87.692308
3289   2/2023  91.969231
3290   3/2023  96.715385
3291   4/2023  98.084615

[2464 rows x 2 columns]

In [89]:
def sampling(df, window_size=1):
    df_as_np = df.to_numpy()
    X = []
    y = []
    for i in range(len(df_as_np)-window_size):
        row = [[a] for a in df_as_np[i:i+window_size]]
        X.append(row)
        label = df_as_np[i+window_size]
        y.append(label)
    return np.array(X), np.array(y)

In [90]:
X1, y1 = sampling(smoothdata['smooth'], STEP)
X1.shape, y1.shape

((2451, 13, 1), (2451,))

In [103]:
# 720 months for 120 months 
X_train1, y_train1 = X1[:720], y1[:720]
X_test1, y_test1 = X1[720:], y1[720:]
X_train1.shape, y_train1.shape, X_test1.shape, y_test1.shape

((720, 13, 1), (720,), (1731, 13, 1), (1731,))

In [104]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import *
from tensorflow.keras.callbacks import ModelCheckpoint
from tensorflow.keras.losses import MeanSquaredError
from tensorflow.keras.metrics import RootMeanSquaredError
from tensorflow.keras.optimizers import Adam

model1 = Sequential()
model1.add(InputLayer((STEP, 1)))
model1.add(LSTM(64))
model1.add(Dense(8, 'relu'))
model1.add(Dense(1, 'linear'))

model1.summary()

Model: "sequential_12"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 lstm_12 (LSTM)              (None, 64)                16896     
                                                                 
 dense_24 (Dense)            (None, 8)                 520       
                                                                 
 dense_25 (Dense)            (None, 1)                 9         
                                                                 
Total params: 17,425
Trainable params: 17,425
Non-trainable params: 0
_________________________________________________________________


In [107]:
cp1 = ModelCheckpoint('model1/', save_best_only=True)
model1.compile(loss=MeanSquaredError(), optimizer=Adam(learning_rate=0.0001), metrics=[RootMeanSquaredError()])

In [116]:
for i in range(0,120):
    model1.fit(X1[i:720+i], y1[i:720+i], epochs=200, callbacks=[cp1])

Epoch 1/200
23/23 [==============================] - 0s 5ms/step - loss: 2566.2952 - root_mean_squared_error: 50.6586
Epoch 2/200
23/23 [==============================] - 0s 5ms/step - loss: 2543.7007 - root_mean_squared_error: 50.4351
Epoch 3/200
23/23 [==============================] - 0s 5ms/step - loss: 2520.3962 - root_mean_squared_error: 50.2035
Epoch 4/200
23/23 [==============================] - 0s 5ms/step - loss: 2497.8201 - root_mean_squared_error: 49.9782
Epoch 5/200
23/23 [==============================] - 0s 5ms/step - loss: 2475.1040 - root_mean_squared_error: 49.7504
Epoch 6/200
23/23 [==============================] - 0s 5ms/step - loss: 2452.8423 - root_mean_squared_error: 49.5262
Epoch 7/200
23/23 [==============================] - 0s 5ms/step - loss: 2430.2600 - root_mean_squared_error: 49.2977
Epoch 8/200
23/23 [==============================] - 0s 5ms/step - loss: 2408.0718 - root_mean_squared_error: 49.0721
Epoch 9/200
23/23 [==============================] - 0s 

23/23 [==============================] - 0s 5ms/step - loss: 1995.2249 - root_mean_squared_error: 44.6679
Epoch 29/200
23/23 [==============================] - 0s 6ms/step - loss: 1975.9989 - root_mean_squared_error: 44.4522
Epoch 30/200
23/23 [==============================] - 0s 6ms/step - loss: 1956.9493 - root_mean_squared_error: 44.2374
Epoch 31/200
23/23 [==============================] - 0s 6ms/step - loss: 1937.9701 - root_mean_squared_error: 44.0224
Epoch 32/200
23/23 [==============================] - 0s 5ms/step - loss: 1919.3181 - root_mean_squared_error: 43.8100
Epoch 33/200
23/23 [==============================] - 0s 5ms/step - loss: 1900.7468 - root_mean_squared_error: 43.5976
Epoch 34/200
23/23 [==============================] - 0s 5ms/step - loss: 1881.9462 - root_mean_squared_error: 43.3814
Epoch 35/200
23/23 [==============================] - 0s 6ms/step - loss: 1863.8694 - root_mean_squared_error: 43.1726
Epoch 36/200
23/23 [==============================] - 0s 5ms/

23/23 [==============================] - 0s 5ms/step - loss: 1509.8071 - root_mean_squared_error: 38.8562
Epoch 57/200
23/23 [==============================] - 0s 5ms/step - loss: 1494.5338 - root_mean_squared_error: 38.6592
Epoch 58/200
23/23 [==============================] - 0s 5ms/step - loss: 1479.2880 - root_mean_squared_error: 38.4615
Epoch 59/200
23/23 [==============================] - 0s 6ms/step - loss: 1463.9882 - root_mean_squared_error: 38.2621
Epoch 60/200
23/23 [==============================] - 0s 5ms/step - loss: 1449.4917 - root_mean_squared_error: 38.0722
Epoch 61/200
23/23 [==============================] - 0s 5ms/step - loss: 1434.5160 - root_mean_squared_error: 37.8750
Epoch 62/200
23/23 [==============================] - 0s 6ms/step - loss: 1419.5547 - root_mean_squared_error: 37.6770
Epoch 63/200
23/23 [==============================] - 0s 5ms/step - loss: 1405.1198 - root_mean_squared_error: 37.4849
Epoch 64/200
23/23 [==============================] - 0s 6ms/

23/23 [==============================] - 0s 6ms/step - loss: 1136.1056 - root_mean_squared_error: 33.7062
Epoch 84/200
23/23 [==============================] - 0s 5ms/step - loss: 1124.0089 - root_mean_squared_error: 33.5262
Epoch 85/200
23/23 [==============================] - 0s 6ms/step - loss: 1111.6140 - root_mean_squared_error: 33.3409
Epoch 86/200
23/23 [==============================] - 0s 6ms/step - loss: 1099.4611 - root_mean_squared_error: 33.1581
Epoch 87/200
23/23 [==============================] - 0s 6ms/step - loss: 1087.3406 - root_mean_squared_error: 32.9748
Epoch 88/200
23/23 [==============================] - 0s 5ms/step - loss: 1075.6526 - root_mean_squared_error: 32.7971
Epoch 89/200
23/23 [==============================] - 0s 4ms/step - loss: 1063.7717 - root_mean_squared_error: 32.6155
Epoch 90/200
23/23 [==============================] - 0s 5ms/step - loss: 1052.1185 - root_mean_squared_error: 32.4364
Epoch 91/200
23/23 [==============================] - 0s 6ms/

23/23 [==============================] - 0s 6ms/step - loss: 825.3528 - root_mean_squared_error: 28.7290
Epoch 112/200
23/23 [==============================] - 0s 6ms/step - loss: 815.7621 - root_mean_squared_error: 28.5616
Epoch 113/200
23/23 [==============================] - 0s 5ms/step - loss: 805.7159 - root_mean_squared_error: 28.3851
Epoch 114/200
23/23 [==============================] - 0s 5ms/step - loss: 796.2013 - root_mean_squared_error: 28.2170
Epoch 115/200
23/23 [==============================] - 0s 5ms/step - loss: 786.6747 - root_mean_squared_error: 28.0477
Epoch 116/200
23/23 [==============================] - 0s 5ms/step - loss: 777.4135 - root_mean_squared_error: 27.8821
Epoch 117/200
23/23 [==============================] - 0s 6ms/step - loss: 767.6735 - root_mean_squared_error: 27.7069
Epoch 118/200
23/23 [==============================] - 0s 5ms/step - loss: 758.5378 - root_mean_squared_error: 27.5416
Epoch 119/200
23/23 [==============================] - 0s 6ms/

...

23/23 [==============================] - 0s 6ms/step - loss: 0.3982 - root_mean_squared_error: 0.6310
Epoch 80/200
23/23 [==============================] - 0s 5ms/step - loss: 0.3137 - root_mean_squared_error: 0.5601
Epoch 81/200
23/23 [==============================] - 0s 5ms/step - loss: 0.3738 - root_mean_squared_error: 0.6114
Epoch 82/200
23/23 [==============================] - 0s 6ms/step - loss: 0.4568 - root_mean_squared_error: 0.6758
Epoch 83/200
23/23 [==============================] - 0s 5ms/step - loss: 0.3637 - root_mean_squared_error: 0.6031
Epoch 84/200
23/23 [==============================] - 0s 6ms/step - loss: 0.3438 - root_mean_squared_error: 0.5864
Epoch 85/200
23/23 [==============================] - 0s 6ms/step - loss: 0.3682 - root_mean_squared_error: 0.6068
Epoch 86/200
23/23 [==============================] - 0s 6ms/step - loss: 0.2991 - root_mean_squared_error: 0.5469
Epoch 87/200
23/23 [==============================] - 0s 6ms/step - loss: 0.3098 - root_mean_

23/23 [==============================] - 0s 5ms/step - loss: 0.4698 - root_mean_squared_error: 0.6855
Epoch 108/200
23/23 [==============================] - 0s 6ms/step - loss: 0.3752 - root_mean_squared_error: 0.6125
Epoch 109/200
23/23 [==============================] - 0s 6ms/step - loss: 0.3737 - root_mean_squared_error: 0.6113
Epoch 110/200
23/23 [==============================] - 0s 6ms/step - loss: 0.3468 - root_mean_squared_error: 0.5889
Epoch 111/200
23/23 [==============================] - 0s 5ms/step - loss: 0.3110 - root_mean_squared_error: 0.5577
Epoch 112/200
23/23 [==============================] - 0s 5ms/step - loss: 0.3135 - root_mean_squared_error: 0.5599
Epoch 113/200
23/23 [==============================] - 0s 5ms/step - loss: 0.3309 - root_mean_squared_error: 0.5752
Epoch 114/200
23/23 [==============================] - 0s 6ms/step - loss: 0.3820 - root_mean_squared_error: 0.6181
Epoch 115/200
23/23 [==============================] - 0s 6ms/step - loss: 0.3573 - ro

23/23 [==============================] - 0s 6ms/step - loss: 0.3131 - root_mean_squared_error: 0.5595
Epoch 136/200
23/23 [==============================] - 0s 5ms/step - loss: 0.2702 - root_mean_squared_error: 0.5198
Epoch 137/200
23/23 [==============================] - 0s 6ms/step - loss: 0.3128 - root_mean_squared_error: 0.5592
Epoch 138/200
23/23 [==============================] - 0s 6ms/step - loss: 0.3233 - root_mean_squared_error: 0.5686
Epoch 139/200
23/23 [==============================] - 0s 6ms/step - loss: 0.2619 - root_mean_squared_error: 0.5118
Epoch 140/200
23/23 [==============================] - 0s 5ms/step - loss: 0.2518 - root_mean_squared_error: 0.5018
Epoch 141/200
23/23 [==============================] - 0s 6ms/step - loss: 0.2990 - root_mean_squared_error: 0.5468
Epoch 142/200
23/23 [==============================] - 0s 6ms/step - loss: 0.2690 - root_mean_squared_error: 0.5186
Epoch 143/200
23/23 [==============================] - 0s 6ms/step - loss: 0.3405 - ro

23/23 [==============================] - 0s 6ms/step - loss: 0.3533 - root_mean_squared_error: 0.5944
Epoch 164/200
23/23 [==============================] - 0s 6ms/step - loss: 0.3313 - root_mean_squared_error: 0.5756
Epoch 165/200
23/23 [==============================] - 0s 6ms/step - loss: 0.3346 - root_mean_squared_error: 0.5785
Epoch 166/200
23/23 [==============================] - 0s 6ms/step - loss: 0.2998 - root_mean_squared_error: 0.5476
Epoch 167/200
23/23 [==============================] - 0s 6ms/step - loss: 0.3388 - root_mean_squared_error: 0.5821
Epoch 168/200
23/23 [==============================] - 0s 5ms/step - loss: 0.3274 - root_mean_squared_error: 0.5722
Epoch 169/200
23/23 [==============================] - 0s 6ms/step - loss: 0.3596 - root_mean_squared_error: 0.5997
Epoch 170/200
23/23 [==============================] - 0s 6ms/step - loss: 0.3436 - root_mean_squared_error: 0.5862
Epoch 171/200
23/23 [==============================] - 0s 6ms/step - loss: 0.3416 - ro

23/23 [==============================] - 0s 5ms/step - loss: 0.3370 - root_mean_squared_error: 0.5805
Epoch 192/200
23/23 [==============================] - 0s 5ms/step - loss: 0.3290 - root_mean_squared_error: 0.5736
Epoch 193/200
23/23 [==============================] - 0s 6ms/step - loss: 0.4245 - root_mean_squared_error: 0.6515
Epoch 194/200
23/23 [==============================] - 0s 6ms/step - loss: 0.3523 - root_mean_squared_error: 0.5936
Epoch 195/200
23/23 [==============================] - 0s 6ms/step - loss: 0.3414 - root_mean_squared_error: 0.5843
Epoch 196/200
23/23 [==============================] - 0s 6ms/step - loss: 0.3550 - root_mean_squared_error: 0.5958
Epoch 197/200
23/23 [==============================] - 0s 6ms/step - loss: 0.3194 - root_mean_squared_error: 0.5652
Epoch 198/200
23/23 [==============================] - 0s 5ms/step - loss: 0.3109 - root_mean_squared_error: 0.5575
Epoch 199/200
23/23 [==============================] - 0s 6ms/step - loss: 0.2574 - ro

In [117]:
scores = model1.evaluate(X_train1, y_train1, verbose=0)
print("%s: %.2f%%" % (model1.metrics_names[1], scores[1]*100))

# serialize model to JSON
model_json = model1.to_json()
with open("model.json", "w") as json_file:
    json_file.write(model_json)
# serialize weights to HDF5
model1.save_weights("model.h5")
print("Saved model to disk")

root_mean_squared_error: 138.97%
Saved model to disk


In [118]:
from sklearn.metrics import mean_squared_error as mse

def plot_predictions1(model, X, y, start=0, end=100):
    predictions = model.predict(X).flatten()
    df = pd.DataFrame(data={'Predictions':predictions, 'Actuals':y})
    fig = px.line(df[start:end],  y=["Predictions","Actuals"], title='Total Sun plot')
    fig.show()
    return df, mse(y, predictions)

In [122]:
plot_predictions1(model1, X1, y1, start=0, end=2451)

77/77 [==============================] - 0s 2ms/step


(      Predictions    Actuals
 0       52.081066  48.676923
 1       52.418808  46.284615
 2       45.985050  45.615385
 3       44.961720  43.700000
 4       47.922955  41.376923
 ...           ...        ...
 2446    83.658531  81.838462
 2447    89.024559  87.692308
 2448    89.316544  91.969231
 2449    95.031410  96.715385
 2450   100.442467  98.084615
 
 [2451 rows x 2 columns],
 17.45115363082011)